# "DE-BUGGING" NEXRAD LEVEL 2 PLOTTING - DOCKERIZED

This tutorial will perform the same plotting of NEXRAD LEVEL 2 data, but it will use Docker containers for the  steps necessary to make a radar animation.

This Jupyter Notebook is being run from a Docker container from which we are able to run Docker commands on the host Griffin VM. This is possible as we shared the Docker socket from the host VM and installed Docker on the Jupter image we are currently using. This configuration of using a Docker container to start external Docker containers is known as "Docker outside of Docker" (dood). 

##### Let's start by building the Docker image for making static plots of NEXRAD data. Let's look at the Dockerfile used to build this image

In [1]:
! cat /home/$NB_USER/work/docker_images/plot_maker/Dockerfile

FROM continuumio/miniconda
MAINTAINER Ziv Dreyfuss "ziv@uchicago.edu"

ENV https_proxy='http://cloud-proxy:3128'
ENV http_proxy='http://cloud-proxy:3128'

RUN conda update conda
RUN conda install -c https://conda.binstar.org/jjhelmus pyart
RUN conda install basemap


##### Using only a few commands in this Dockerfile we are able to pull a Miniconda environment and add modules with which we can plot NEXRAD data.

In [2]:
! cd /home/$NB_USER/work/docker_images/plot_maker/ ; \
sudo docker build -t 'plot_maker' .

Sending build context to Docker daemon 2.048 kB
Sending build context to Docker daemon 
Step 0 : FROM continuumio/miniconda
 ---> 7453f1822ab7
Step 1 : MAINTAINER Ziv Dreyfuss "ziv@uchicago.edu"
 ---> Using cache
 ---> 9556f583348a
Step 2 : ENV https_proxy 'http://cloud-proxy:3128'
 ---> Using cache
 ---> 1dd6a0135563
Step 3 : ENV http_proxy 'http://cloud-proxy:3128'
 ---> Using cache
 ---> f217ef33ab5c
Step 4 : RUN conda update conda
 ---> Using cache
 ---> 06bf2816180d
Step 5 : RUN conda install -c https://conda.binstar.org/jjhelmus pyart
 ---> Using cache
 ---> 76292dd09953
Step 6 : RUN conda install basemap
 ---> Using cache
 ---> fcf09de68f7a
Successfully built fcf09de68f7a


##### But before we can run a Docker container from the image we just created, we have to download NEXRAD L2 files into the directory that we share with the Griffin VM and will share with other Docker containers. We will use nearly identical functions as before.

In [3]:
import hashlib #to confirm hash of NEXRAD L2 files
import requests
import os

# read in .txt file of ark IDs
with open('mayfly_arks.txt', 'r') as f:
    file_lines = f.readlines()
    id_service_arks = [line.strip() for line in file_lines]

    
# want to be able to confirm we are getting right data
# hash provided in signpost should match locally calculated hash
def confirm_hash(hash_algo, file_,actual_hash):
    with open(file_, 'rb') as f:
        computed_hash = hash_algo(f.read()).hexdigest()
 
    if computed_hash == actual_hash:
        return True
    else:
        return False


# download, validate(optional) NEXRAD L2 data 
def download_from_arks(id_service_arks, intended_dir, hash_confirmation = True,pref_repo='https://griffin-objstore.opensciencedatacloud.org/'):
    hash_algo_dict = {'md5':hashlib.md5, 'sha1':hashlib.sha1, 'sha256':hashlib.sha256}
    nexrad_file_list = [] #make list of downloaded files
    
    for ark_id in id_service_arks:
        signpost_url = 'https://signpost.opensciencedatacloud.org/alias/' + ark_id
        resp = requests.get(signpost_url,
                           proxies={'http':'http://cloud-proxy:3128','https':'http://cloud-proxy:3128'} 
                           )
        
        # make JSON response into dictionary
        signpost_dict = resp.json()
        
        # get repository URLs
        repo_urls = data_url = signpost_dict['urls']
       
        for url in repo_urls:
            # if preferred repo exists, will opt for that URL
            if pref_repo in url:
                break
        # otherwise, will use last url provided
        
        # wow! we can run this bash command from Jupyter!
        !sudo wget -P $intended_dir $url
        
        # need file path for hash validation
        file_name = url.split('/')[-1]
        file_path = os.path.join(intended_dir, file_name)
        nexrad_file_list.append(file_path)
        
        if hash_confirmation:
            # get dict of hash type: hash
            hashes = signpost_dict['hashes']
            # iterate though list of (hash type, hash) tuples
            for hash_tup in hashes.items():
                # get proper hash algorithm function
                hash_algo = hash_algo_dict[hash_tup[0]]

                # fail if not the downloaded file has diff. hash
                assert confirm_hash(hash_algo, file_path, hash_tup[1]), '%s hash calculated does not match hash in metadata' % file_path
    return nexrad_file_list

In [4]:
# read ark ids out of .txt file in nexrad directory
ark_ids = [ark_id.strip() for ark_id in open('mayfly_arks.txt').readlines()]

In [5]:
# run download function
nexrad_file_list = download_from_arks(ark_ids, 'input_files')

--2016-06-02 14:59:05--  https://griffin-objstore.opensciencedatacloud.org/noaa-nexrad-l2/2015/06/26/KARX/KARX20150626_021937_V06.gz
Resolving cloud-proxy (cloud-proxy)... 10.24.0.2
Connecting to cloud-proxy (cloud-proxy)|10.24.0.2|:3128... connected.
Proxy request sent, awaiting response... 200 OK
Length: 6376660 (6.1M) [application/octet-stream]
Saving to: ‘input_files/KARX20150626_021937_V06.gz.1’

input_files/KARX201 100%[=====================>]   6.08M  --.-KB/s   in 0.1s   

2016-06-02 14:59:05 (55.8 MB/s) - ‘input_files/KARX20150626_021937_V06.gz.1’ saved [6376660/6376660]

--2016-06-02 14:59:27--  https://griffin-objstore.opensciencedatacloud.org/noaa-nexrad-l2/2015/06/26/KARX/KARX20150626_022359_V06.gz
Resolving cloud-proxy (cloud-proxy)... 10.24.0.2
Connecting to cloud-proxy (cloud-proxy)|10.24.0.2|:3128... connected.
Proxy request sent, awaiting response... 200 OK
Length: 6600213 (6.3M) [application/octet-stream]
Saving to: ‘input_files/KARX20150626_022359_V06.gz.1’

input_f

##### NOTE: As we are mounting directories onto our Docker containers, we have to provide the absolute path of the files AS THEY WILL BE WITHIN THE DOCKER CONTAINERS

In [6]:
# while this absolute path won't work in our current container, will when we mount /home/ubuntu/nexrad onto /home/nexrad
nexrad_container_file_list = [os.path.join('/home/nexrad', file_name) for file_name in nexrad_file_list]

# quick manipulation to allow us to feed file list into stdin of function
nexrad_file_input = ' '.join(nexrad_container_file_list)
! echo $nexrad_file_input

/home/nexrad/input_files/KARX20150626_021937_V06.gz /home/nexrad/input_files/KARX20150626_022359_V06.gz /home/nexrad/input_files/KARX20150626_022820_V06.gz /home/nexrad/input_files/KARX20150626_023242_V06.gz /home/nexrad/input_files/KARX20150626_023704_V06.gz /home/nexrad/input_files/KARX20150626_024126_V06.gz /home/nexrad/input_files/KARX20150626_024548_V06.gz /home/nexrad/input_files/KARX20150626_025011_V06.gz /home/nexrad/input_files/KARX20150626_025433_V06.gz /home/nexrad/input_files/KARX20150626_025855_V06.gz /home/nexrad/input_files/KARX20150626_030318_V06.gz /home/nexrad/input_files/KARX20150626_030739_V06.gz /home/nexrad/input_files/KARX20150626_031201_V06.gz /home/nexrad/input_files/KARX20150626_031624_V06.gz /home/nexrad/input_files/KARX20150626_032044_V06.gz /home/nexrad/input_files/KARX20150626_032506_V06.gz /home/nexrad/input_files/KARX20150626_032929_V06.gz /home/nexrad/input_files/KARX20150626_033352_V06.gz /home/nexrad/input_files/KARX20150626_033814_V06.gz /home/nexrad

##### Now we are ready to run the plot making container. Within the container we run a Python script that employs the same function as we used to plot unfiltered NEXRAD L2 data as before. Notice how we share the directory /home/ubuntu/nexrad/ with the container.

In [7]:
! sudo docker run  -v /home/ubuntu/nexrad:/home/nexrad plot_maker python /home/nexrad/unfiltered_nexrad_plotter.py -f $nexrad_file_input  -d /home/nexrad/output_plots -p plot_files.txt

/opt/conda/lib/python2.7/site-packages/matplotlib/font_manager.py:273: UserWarning: Matplotlib is building the font cache using fc-list. This may take a moment.
  warnings.warn('Matplotlib is building the font cache using fc-list. This may take a moment.')
/opt/conda/lib/python2.7/site-packages/matplotlib/pyplot.py:516: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)


##### Let's see the list of plots we just made! 

In [8]:
! cat /home/$NB_USER/work/nexrad/output_plots/plot_files.txt

/home/nexrad/output_plots/KARX20150626_021937_V06.png
/home/nexrad/output_plots/KARX20150626_022359_V06.png
/home/nexrad/output_plots/KARX20150626_022820_V06.png
/home/nexrad/output_plots/KARX20150626_023242_V06.png
/home/nexrad/output_plots/KARX20150626_023704_V06.png
/home/nexrad/output_plots/KARX20150626_024126_V06.png
/home/nexrad/output_plots/KARX20150626_024548_V06.png
/home/nexrad/output_plots/KARX20150626_025011_V06.png
/home/nexrad/output_plots/KARX20150626_025433_V06.png
/home/nexrad/output_plots/KARX20150626_025855_V06.png
/home/nexrad/output_plots/KARX20150626_030318_V06.png
/home/nexrad/output_plots/KARX20150626_030739_V06.png
/home/nexrad/output_plots/KARX20150626_031201_V06.png
/home/nexrad/output_plots/KARX20150626_031624_V06.png
/home/nexrad/output_plots/KARX20150626_032044_V06.png
/home/nexrad/output_plots/KARX20150626_032506_V06.png
/home/nexrad/output_plots/KARX20150626_032929_V06.png
/home/nexrad/output_plots/KARX20150626_033352_V06.png
/home/nexrad/output_plots/KA

##### GREAT! Now let's build the Docker image with which we will create animations from our static plots.

In [9]:
! cd /home/$NB_USER/work/docker_images/animation_maker/ ;\
sudo docker build -t 'animation_maker' .

Sending build context to Docker daemon  2.56 kB
Sending build context to Docker daemon 
Step 0 : FROM ubuntu
 ---> 686477c12982
Step 1 : ENV https_proxy 'http://cloud-proxy:3128'
 ---> Using cache
 ---> 81896035d03d
Step 2 : ENV http_proxy 'http://cloud-proxy:3128'
 ---> Using cache
 ---> 8ef0ce6504bb
Step 3 : RUN apt-get update
 ---> Using cache
 ---> 315e373511d4
Step 4 : RUN apt-get install -y python
 ---> Using cache
 ---> c645cc8f3140
Step 5 : RUN apt-get install -y libav-tools
 ---> Using cache
 ---> 54de83115570
Step 6 : RUN apt-get install -y python-qt4
 ---> Using cache
 ---> bd290f85aace
Step 7 : RUN apt-get install -y python-pip
 ---> Using cache
 ---> 65c10568faee
Step 8 : RUN pip install ipython
 ---> Using cache
 ---> a2e1dd23cee0
Step 9 : RUN pip install --upgrade pip
 ---> Using cache
 ---> b8eab76828f2
Step 10 : RUN apt-get install -y libfreetype6-dev
 ---> Using cache
 ---> 556777d063be
Step 11 : RUN apt-get install -y libpng-dev
 ---> Using cache
 ---> 55db918b28d0
S

In [10]:
! sudo docker run -v /home/ubuntu/nexrad:/home/nexrad animation_maker python /home/nexrad/animation_maker.py -f /home/nexrad/output_plots/plot_files.txt -n /home/nexrad/animation_html/anim_1

/usr/local/lib/python2.7/dist-packages/matplotlib/font_manager.py:273: UserWarning: Matplotlib is building the font cache using fc-list. This may take a moment.
  warnings.warn('Matplotlib is building the font cache using fc-list. This may take a moment.')


In [2]:
html = open('/home/jovyan/work/nexrad/animation_html/anim_1').read()

In [3]:
from IPython.display import HTML
HTML(html)

##### Great, now we make filtered plots through the same Docker image with which we made the unfiltered plots. We use a new Python script, filtered_nexrad_plotter.py, that is added to the container when we put it into the shared volume.

In [13]:
! sudo docker run  -v /home/ubuntu/nexrad:/home/nexrad plot_maker python /home/nexrad/filtered_nexrad_plotter.py -f $nexrad_file_input  -d /home/nexrad/output_plots -p only_weather_plot_files.txt -n weather_

/opt/conda/lib/python2.7/site-packages/matplotlib/font_manager.py:273: UserWarning: Matplotlib is building the font cache using fc-list. This may take a moment.
  warnings.warn('Matplotlib is building the font cache using fc-list. This may take a moment.')
/opt/conda/lib/python2.7/site-packages/matplotlib/pyplot.py:516: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)


##### Let's run the same script, but filtering out weather phenomena to reveal the bioscatter captured in the NEXRAD L2 data.

In [14]:
# notice '-b' flag at the end 
! sudo docker run  -v /home/ubuntu/nexrad:/home/nexrad plot_maker python /home/nexrad/filtered_nexrad_plotter.py -f $nexrad_file_input  -d /home/nexrad/output_plots -p bioscatter_plot_files.txt -n 'bioscatter_' -b

/opt/conda/lib/python2.7/site-packages/matplotlib/font_manager.py:273: UserWarning: Matplotlib is building the font cache using fc-list. This may take a moment.
  warnings.warn('Matplotlib is building the font cache using fc-list. This may take a moment.')
/opt/conda/lib/python2.7/site-packages/matplotlib/pyplot.py:516: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  max_open_warning, RuntimeWarning)


##### Alright! Now let's make/view the animations; First up - only weather.

In [15]:
! sudo docker run -v /home/ubuntu/nexrad:/home/nexrad animation_maker python /home/nexrad/animation_maker.py -f /home/nexrad/output_plots/only_weather_plot_files.txt -n /home/nexrad/animation_html/anim_weather

/usr/local/lib/python2.7/dist-packages/matplotlib/font_manager.py:273: UserWarning: Matplotlib is building the font cache using fc-list. This may take a moment.
  warnings.warn('Matplotlib is building the font cache using fc-list. This may take a moment.')


In [4]:
html = open('/home/jovyan/work/nexrad/animation_html/anim_weather').read()
HTML(html)

##### Finally, let's make the animation of only bioscatter.

In [17]:
! sudo docker run -v /home/ubuntu/nexrad:/home/nexrad animation_maker python /home/nexrad/animation_maker.py -f /home/nexrad/output_plots/bioscatter_plot_files.txt -n /home/nexrad/animation_html/anim_bioscatter

/usr/local/lib/python2.7/dist-packages/matplotlib/font_manager.py:273: UserWarning: Matplotlib is building the font cache using fc-list. This may take a moment.
  warnings.warn('Matplotlib is building the font cache using fc-list. This may take a moment.')


In [5]:
html = open('/home/jovyan/work/nexrad/animation_html/anim_bioscatter').read()
HTML(html)